In [1]:
import pandas as pd
import geopandas as gpd

# read the shape file
sf = gpd.read_file("../data/raw/PTV_METRO_BUS_STOP.shp")

sf.head()

STOP_ID                                          STOP_NAME   LATITUDE  \
0   10185       Bonnie View Rd/Maroondah Hwy (Croydon North) -37.780920   
1   10186          Primrose Rd/Maroondah Hwy (Croydon North) -37.774626   
2   10187            Exeter Rd/Maroondah Hwy (Croydon North) -37.770446   
3   10188  Maroondah Golf Park/Maroondah Hwy (Chirnside P... -37.766346   
4   10189    Old Melbourne Rd/Maroondah Hwy (Chirnside Park) -37.765276   

    LONGITUDE TICKETZONE ROUTEUSSP                        geometry  
0  145.288145          2       670  POINT (349252.545 5817113.477)  
1  145.292843          2       670  POINT (349653.536 5817819.423)  
2  145.295459          2       670  POINT (349875.465 5818287.445)  
3  145.301775          2       670  POINT (350423.536 5818752.496)  
4  145.304410          2       670  POINT (350653.473 5818875.436)

In [2]:
# Convert the geometry shaape to to latitude and longitude
# Please attribute this if you are using it
sf['geometry'] = sf['geometry'].to_crs("+proj=longlat +ellps=WGS84 +datum=WGS84 +no_defs")
sf.head()

STOP_ID                                          STOP_NAME   LATITUDE  \
0   10185       Bonnie View Rd/Maroondah Hwy (Croydon North) -37.780920   
1   10186          Primrose Rd/Maroondah Hwy (Croydon North) -37.774626   
2   10187            Exeter Rd/Maroondah Hwy (Croydon North) -37.770446   
3   10188  Maroondah Golf Park/Maroondah Hwy (Chirnside P... -37.766346   
4   10189    Old Melbourne Rd/Maroondah Hwy (Chirnside Park) -37.765276   

    LONGITUDE TICKETZONE ROUTEUSSP                     geometry  
0  145.288145          2       670  POINT (145.28815 -37.78091)  
1  145.292843          2       670  POINT (145.29285 -37.77461)  
2  145.295459          2       670  POINT (145.29546 -37.77043)  
3  145.301775          2       670  POINT (145.30178 -37.76633)  
4  145.304410          2       670  POINT (145.30442 -37.76526)

In [3]:
# create a JSON 
geoJSON = sf['geometry'].to_json()

# print the first 300 chars of the json
print(geoJSON[:300])

{"type": "FeatureCollection", "features": [{"id": "0", "type": "Feature", "properties": {}, "geometry": {"type": "Point", "coordinates": [145.28815104390307, -37.780906859639494]}, "bbox": [145.28815104390307, -37.780906859639494, 145.28815104390307, -37.780906859639494]}, {"id": "1", "type": "Featu


In [4]:
import folium

_map = folium.Map(location=[143.73, -37.56], tiles="Stamen Terrain", zoom_start=10)

# refer to the folium documentations on how to plot aggregated data.
_map.add_child(folium.Choropleth(
    geo_data=geoJSON,
    name='choropleth',
))

_map

In [5]:
bus_station = sf[['STOP_NAME', 'LATITUDE', 'LONGITUDE']]

bus_station.head()

STOP_NAME   LATITUDE   LONGITUDE
0       Bonnie View Rd/Maroondah Hwy (Croydon North) -37.780920  145.288145
1          Primrose Rd/Maroondah Hwy (Croydon North) -37.774626  145.292843
2            Exeter Rd/Maroondah Hwy (Croydon North) -37.770446  145.295459
3  Maroondah Golf Park/Maroondah Hwy (Chirnside P... -37.766346  145.301775
4    Old Melbourne Rd/Maroondah Hwy (Chirnside Park) -37.765276  145.304410

In [6]:
from pandas.core.frame import DataFrame

# Create new list for later use
bus_station_list = []

# Loop through the dataframe, add unformation into the list
for i in range(0,len(bus_station)):
    row = bus_station.iloc[i]
    location = str(row[1]) + ', ' + str(row[2])
    bus_station_list.append([row[0], location])

# Forming new dataframe
bus_station_new = DataFrame(data = bus_station_list, columns=['Bus_Station_Name', 'Location'])

bus_station_new.head()


Bus_Station_Name                Location
0       Bonnie View Rd/Maroondah Hwy (Croydon North)   -37.78092, 145.288145
1          Primrose Rd/Maroondah Hwy (Croydon North)  -37.774626, 145.292843
2            Exeter Rd/Maroondah Hwy (Croydon North)  -37.770446, 145.295459
3  Maroondah Golf Park/Maroondah Hwy (Chirnside P...  -37.766346, 145.301775
4    Old Melbourne Rd/Maroondah Hwy (Chirnside Park)   -37.765276, 145.30441

In [ ]:
pip install geopy

In [9]:
from geopy.geocoders import Nominatim

postcode_list = []
geolocator = Nominatim(user_agent="vscode")
count = 1

for i in range(0,len(bus_station_new)):
    row = bus_station_new.iloc[i]
    location = geolocator.reverse(row[1])

    if 'postcode' in location.raw['address'].keys():
        post = location.raw['address']['postcode']
        postcode_list.append([row[0], row[1], int(post)])
    else:
        count += 1

bus_station_postcode = DataFrame(data = postcode_list, columns=['Bus_Station_Name', 'Location', 'Postcode'])

bus_station_postcode.head()

Bus_Station_Name                Location  \
0       Bonnie View Rd/Maroondah Hwy (Croydon North)   -37.78092, 145.288145   
1          Primrose Rd/Maroondah Hwy (Croydon North)  -37.774626, 145.292843   
2            Exeter Rd/Maroondah Hwy (Croydon North)  -37.770446, 145.295459   
3  Maroondah Golf Park/Maroondah Hwy (Chirnside P...  -37.766346, 145.301775   
4    Old Melbourne Rd/Maroondah Hwy (Chirnside Park)   -37.765276, 145.30441   

   Postcode  
0      3136  
1      3136  
2      3116  
3      3116  
4      3116

In [10]:
bus_station_postcode.to_csv('../data/curated/bus_station_postcode.csv')